# Neo4j Generative AI Workshop

## Setup

In [1]:
%%capture
%pip install sentence_transformers langchain openai tiktoken python-dotenv gradio graphdatascience altair
%pip install "vegafusion[embed]"

In [107]:
from graphdatascience import GraphDataScience
from dotenv import load_dotenv
import os
import pandas as pd
import numpy as np
from datetime import datetime, timedelta
from langchain.embeddings import OpenAIEmbeddings, BedrockEmbeddings, SentenceTransformerEmbeddings

### Setup Credentials and Environment Variables

To make this easy, you can write the credentials and env variables directly into the below cell

If you like you can use an environments file instead by copying `ws.env.template` to `ws.env` and filling credentials and variables in there. This is a best practice for the future, but fine to skip for this workshop.

In [108]:
# Neo4j
NEO4J_URI = 'bolt://localhost:7687' #change this
NEO4J_PASSWORD = 'password' #cahnge this
NEO4J_USERNAME = 'neo4j'
AURA_DS = False

# AI
EMBEDDING_MODEL = 'openai' #or sentence_transformer or aws
LLM = 'gpt-3.5' #LLM=gpt-3.5 #or gpt-4 or claudev2

# OpenAI - Required when using OpenAI models
os.environ['OPENAI_API_KEY'] = 'sk-...' #cahnge this

# AWS - Only required when using AWS Bedrock models
#os.environ['AWS_ACCESS_KEY_ID'] =
#os.environ['AWS_SECRET_ACCESS_KEY'] =
#os.environ['AWS_DEFAULT_REGION=us-east-1'] =

In [109]:
# You can skip this if not using a ws.env file
if os.path.exists('ws.env'):
    load_dotenv('ws.env', override=True)

    # Neo4j
    NEO4J_URI = os.getenv('NEO4J_URI')
    NEO4J_USERNAME = os.getenv('NEO4J_USERNAME')
    NEO4J_PASSWORD = os.getenv('NEO4J_PASSWORD')
    AURA_DS = eval(os.getenv('AURA_DS').title())

    # AI
    EMBEDDING_MODEL = os.getenv('EMBEDDING_MODEL')
    LLM = os.getenv('LLM')

## Knowledge Graph Building

### Get Source Data

In [110]:
department_df = pd.read_csv('https://storage.googleapis.com/neo4j-workshop-data/genai-hm/department.csv')
department_df

departmentNo              departmentName  sectionNo  \
0            1676                Jersey Basic         16   
1            1339              Clean Lingerie         61   
2            3608                Tights basic         62   
3            5883                Jersey Basic         26   
4            2032                      Jersey          8   
..            ...                         ...        ...   
261          7510                       Woven         28   
262          3420  Small Accessories Extended         66   
263          5231                      Jacket         31   
264          8090       Promotion/Other/Offer         29   
265          5888                      Blanks         26   

                        sectionName  
0            Womens Everyday Basics  
1                   Womens Lingerie  
2    Womens Nightwear, Socks & Tigh  
3                     Men Underwear  
4                              Mama  
..                              ...  
261                     Men Edition  
262        Womens Small accessories  
263                  Mens Outerwear  
264                       Men Other  
265                   Men Underwear  

[266 rows x 4 columns]

In [111]:
product_df = pd.read_csv('https://storage.googleapis.com/neo4j-workshop-data/genai-hm/product.csv')
product_df

productCode                   prodName  productTypeNo   productTypeName  \
0          108775                  Strap top            253          Vest top   
1          110065          OP T-shirt (Idro)            306               Bra   
2          111565        20 den 1p Stockings            304  Underwear Tights   
3          111586  Shape Up 30 den 1p Tights            273   Leggings/Tights   
4          111593   Support 40 den 1p Tights            304  Underwear Tights   
...           ...                        ...            ...               ...   
8039       936862            EDC Marla dress            265             Dress   
8040       936979     Class Filippa Necklace             77          Necklace   
8041       937138   Flirty Albin bracelet pk             68          Bracelet   
8042       942187               ED Sasha tee            255           T-shirt   
8043       952938                  Elton top            254               Top   

        productGroupName  garmentGroupNo   garmentGroupName  \
0     Garment Upper body            1002       Jersey Basic   
1              Underwear            1017  Under-, Nightwear   
2         Socks & Tights            1021   Socks and Tights   
3     Garment Lower body            1021   Socks and Tights   
4         Socks & Tights            1021   Socks and Tights   
...                  ...             ...                ...   
8039   Garment Full body            1023     Special Offers   
8040         Accessories            1019        Accessories   
8041         Accessories            1019        Accessories   
8042  Garment Upper body            1005       Jersey Fancy   
8043  Garment Upper body            1005       Jersey Fancy   

                                             detailDesc  
0               Jersey top with narrow shoulder straps.  
1     Microfibre T-shirt bra with underwired, moulde...  
2     Semi shiny nylon stockings with a wide, reinfo...  
3     Tights with built-in support to lift the botto...  
4     Semi shiny tights that shape the tummy, thighs...  
...                                                 ...  
8039  Calf-length dress in a patterned Tencel™ lyoce...  
8040  Metal chain necklace with a pendant. Adjustabl...  
8041  Metal chain bracelets. Two plain and two with ...  
8042  Oversized, straight-cut T-shirt in a soft moda...  
8043  Fitted top in jersey with a round neckline and...  

[8044 rows x 8 columns]

In [112]:
article_df = pd.read_csv('https://storage.googleapis.com/neo4j-workshop-data/genai-hm/article.csv')
article_df

articleId  productCode  departmentNo                   prodName  \
0      108775015       108775          1676                  Strap top   
1      108775044       108775          1676                  Strap top   
2      110065001       110065          1339          OP T-shirt (Idro)   
3      111565001       111565          3608        20 den 1p Stockings   
4      111586001       111586          3608  Shape Up 30 den 1p Tights   
...          ...          ...           ...                        ...   
13346  936862001       936862          3090            EDC Marla dress   
13347  936979001       936979          4344     Class Filippa Necklace   
13348  937138001       937138          4345   Flirty Albin bracelet pk   
13349  942187001       942187          1919               ED Sasha tee   
13350  952938001       952938          1641                  Elton top   

        productTypeName  graphicalAppearanceNo graphicalAppearanceName  \
0              Vest top                1010016                   Solid   
1              Vest top                1010016                   Solid   
2                   Bra                1010016                   Solid   
3      Underwear Tights                1010016                   Solid   
4       Leggings/Tights                1010016                   Solid   
...                 ...                    ...                     ...   
13346             Dress                1010001        All over pattern   
13347          Necklace                1010016                   Solid   
13348          Bracelet                1010016                   Solid   
13349           T-shirt                1010016                   Solid   
13350               Top                1010001        All over pattern   

       colourGroupCode colourGroupName  
0                    9           Black  
1                   10           White  
2                    9           Black  
3                    9           Black  
4                    9           Black  
...                ...             ...  
13346               52            Pink  
13347                5            Gold  
13348                5            Gold  
13349                9           Black  
13350               13           Beige  

[13351 rows x 9 columns]

In [113]:
customer_df = pd.read_csv('https://storage.googleapis.com/neo4j-workshop-data/genai-hm/customer.csv')
customer_df

customerId   fn  active  \
0    00264b7d4cd6498292e8a355b699c2d07725d123f04867...  1.0     1.0   
1    005c6d3bb66c86aab606814cd9995a12f99b3a44b58c72...  NaN     NaN   
2    00abec3de294e03d192db15b91e154853ee1c89415e7cd...  NaN     NaN   
3    00f311a42124fc44d117135f34e1fca29fcac271e6fbd0...  1.0     1.0   
4    0132cd2eb3c6b1f66784f65f94ddd8352add2653e0caf5...  NaN     NaN   
..                                                 ...  ...     ...   
995  fdf1294f414faac2b00a725f5d80c34f98a744d9b8b3ce...  NaN     NaN   
996  fe6faeed37fe86e885928d3ab30d8d9b072d6643c8aa15...  1.0     1.0   
997  fef793ec3a7d62d782824517355d74ded50964dce33009...  NaN     NaN   
998  ffb925b11e1bb2e375d22a02d67907994eb8cb92ec2e7d...  NaN     NaN   
999  ffe8f77be0ce1a5bde91c97cb76aa887fb200bba79fe5a...  1.0     1.0   

    clubMemberStatus fashionNewsFrequency   age  \
0             ACTIVE            Regularly  53.0   
1         PRE-CREATE                 NONE   NaN   
2             ACTIVE                 NONE  49.0   
3             ACTIVE            Regularly  55.0   
4             ACTIVE                 NONE  49.0   
..               ...                  ...   ...   
995           ACTIVE                 NONE  32.0   
996           ACTIVE            Regularly  46.0   
997           ACTIVE                 NONE  46.0   
998           ACTIVE                 NONE  34.0   
999           ACTIVE            Regularly  26.0   

                                            postalCode  
0    2c29ae653a9282cce4151bd87643c907644e09541abc28...  
1    177b4a2258a85a2247daaa7cdffba96a74c741ea8a6605...  
2    86557a458110ac98f4ca80e5a815ba2e8ea086dd8039b0...  
3    1a80c5651ae36327a86e71d5b967cf62c31126d1b57ae0...  
4    49f7ec29bcacbbf2120af5162f9f99c212e9dd26b48d79...  
..                                                 ...  
995  0cd87888c3a13ebbb1e90cac6b9fbf34c51afa40865f55...  
996  fe234b03107b233aec5695dc4c3fbe8e638338643f4e14...  
997  5799a39cffe701ebdb12181348bf10f9e23abcc3868c43...  
998  ebdd8c5c893683c3cf52c011d4e35024e46d183c95f0fa...  
999  bf90cabe02380b161574072e5ca4f77f62b313421e3f62...  

[1000 rows x 7 columns]

In [114]:
transaction_df = pd.read_csv('https://storage.googleapis.com/neo4j-workshop-data/genai-hm/transaction.csv')
transaction_df

tDat                                         customerId  \
0      2018-09-20  0ddcd6055c5830c1fda493843d051edb04ce1bf888aa4b...   
1      2018-09-20  210f113fe87db5d6391e986dc06b8e4369e46284e3b989...   
2      2018-09-20  210f113fe87db5d6391e986dc06b8e4369e46284e3b989...   
3      2018-09-20  211a2ef477fcfc8fc40a63ffa70bb41086dd06ca85d4af...   
4      2018-09-20  211a2ef477fcfc8fc40a63ffa70bb41086dd06ca85d4af...   
...           ...                                                ...   
23194  2020-09-22  b6be55f233772b5fc4a1ebedf36542fb3e1b6c15c23c7e...   
23195  2020-09-22  b6be55f233772b5fc4a1ebedf36542fb3e1b6c15c23c7e...   
23196  2020-09-22  b6be55f233772b5fc4a1ebedf36542fb3e1b6c15c23c7e...   
23197  2020-09-22  b6be55f233772b5fc4a1ebedf36542fb3e1b6c15c23c7e...   
23198  2020-09-22  bc5e2e45ecc9b00eb0b01a3373edbb654aad248d75f12b...   

       articleId     price  salesChannelId      txId  
0      653428002  0.135576               1      2445  
1      636587001  0.008458               1      6182  
2      640462002  0.032186               1      6183  
3      645422002  0.014390               2      6188  
4      645422002  0.014390               2      6189  
...          ...       ...             ...       ...  
23194  921266007  0.016932               2  31779124  
23195  812530004  0.010153               2  31779125  
23196  942187001  0.016932               2  31779126  
23197  866731001  0.025407               2  31779127  
23198  678942001  0.016932               2  31779858  

[23199 rows x 6 columns]

### Connect to Neo4j

In [115]:
# Use Neo4j URI and credentials according to our setup
gds = GraphDataScience(
    NEO4J_URI,
    auth=(NEO4J_USERNAME, NEO4J_PASSWORD),
    aura_ds=AURA_DS)

# Necessary if you enabled Arrow on the db - this is true for AuraDS
gds.set_database("neo4j")

### Create Constraints

In [116]:
# one uniqueness constraint for each node label
gds.run_cypher('CREATE CONSTRAINT unique_department_no IF NOT EXISTS FOR (n:Department) REQUIRE n.departmentNo IS UNIQUE')
gds.run_cypher('CREATE CONSTRAINT unique_product_code IF NOT EXISTS FOR (n:Product) REQUIRE n.productCode IS UNIQUE')
gds.run_cypher('CREATE CONSTRAINT unique_article_id IF NOT EXISTS FOR (n:Article) REQUIRE n.articleId IS UNIQUE')
gds.run_cypher('CREATE CONSTRAINT unique_customer_id IF NOT EXISTS FOR (n:Customer) REQUIRE n.customerId IS UNIQUE')

Empty DataFrame
Columns: []
Index: []

### Helper Functions

In [117]:
from typing import Tuple, Union
from numpy.typing import ArrayLike


def make_map(x):
    if type(x) == str:
        return x, x
    elif type(x) == tuple:
        return x
    else:
        raise Exception("Entry must of type string or tuple")


def make_set_clause(prop_names: ArrayLike, element_name='n', item_name='rec'):
    clause_list = []
    for prop_name in prop_names:
        clause_list.append(f'{element_name}.{prop_name} = {item_name}.{prop_name}')
    return 'SET ' + ', '.join(clause_list)


def make_node_merge_query(node_key_name: str, node_label: str, cols: ArrayLike):
    template = f'''UNWIND $recs AS rec\nMERGE(n:{node_label} {{{node_key_name}: rec.{node_key_name}}})'''
    prop_names = [x for x in cols if x != node_key_name]
    if len(prop_names) > 0:
        template = template + '\n' + make_set_clause(prop_names)
    return template + '\nRETURN count(n) AS nodeLoadedCount'


def make_rel_merge_query(source_target_labels: Union[Tuple[str, str], str],
                         source_node_key: Union[Tuple[str, str], str],
                         target_node_key: Union[Tuple[str, str], str],
                         rel_type: str,
                         cols: ArrayLike,
                         rel_key: str = None):
    source_target_label_map = make_map(source_target_labels)
    source_node_key_map = make_map(source_node_key)
    target_node_key_map = make_map(target_node_key)

    merge_statement = f'MERGE(s)-[r:{rel_type}]->(t)'
    if rel_key is not None:
        merge_statement = f'MERGE(s)-[r:{rel_type} {{{rel_key}: rec.{rel_key}}}]->(t)'

    template = f'''\tUNWIND $recs AS rec
    MATCH(s:{source_target_label_map[0]} {{{source_node_key_map[0]}: rec.{source_node_key_map[1]}}})
    MATCH(t:{source_target_label_map[1]} {{{target_node_key_map[0]}: rec.{target_node_key_map[1]}}})\n\t''' + merge_statement
    prop_names = [x for x in cols if x not in [rel_key, source_node_key_map[1], target_node_key_map[1]]]
    if len(prop_names) > 0:
        template = template + '\n\t' + make_set_clause(prop_names, 'r')
    return template + '\n\tRETURN count(r) AS relLoadedCount'


def chunks(xs, n=10_000):
    n = max(1, n)
    return [xs[i:i + n] for i in range(0, len(xs), n)]


def load_nodes(gds: GraphDataScience, node_df: pd.DataFrame, node_key_col: str, node_label: str, chunk_size=10_000):
    records = node_df.to_dict('records')
    print(f'======  loading {node_label} nodes  ======')
    total = len(records)
    print(f'staging {total:,} records')
    query = make_node_merge_query(node_key_col, node_label, node_df.columns.copy())
    cumulative_count = 0
    for recs in chunks(records, chunk_size):
        res = gds.run_cypher(query, params={'recs': recs})
        cumulative_count += res.iloc[0, 0]
        print(f'Loaded {cumulative_count:,} of {total:,} nodes')


def load_rels(gds: GraphDataScience,
              rel_df: pd.DataFrame,
              source_target_labels: Union[Tuple[str, str], str],
              source_node_key: Union[Tuple[str, str], str],
              target_node_key: Union[Tuple[str, str], str],
              rel_type: str,
              rel_key: str = None,
              chunk_size=10_000):
    records = rel_df.to_dict('records')
    print(f'======  loading {rel_type} relationships  ======')
    total = len(records)
    print(f'staging {total:,} records')
    query = make_rel_merge_query(source_target_labels, source_node_key,
                                 target_node_key, rel_type, rel_df.columns.copy(), rel_key)
    cumulative_count = 0
    for recs in chunks(records, chunk_size):
        res = gds.run_cypher(query, params={'recs': recs})
        cumulative_count += res.iloc[0, 0]
        print(f'Loaded {cumulative_count:,} of {total:,} relationships')

### Load Nodes

In [118]:
%%time
load_nodes(gds, department_df, 'departmentNo', 'Department')

======  loading Department nodes  ======
staging 266 records
Loaded 266 of 266 nodes
CPU times: user 7.49 ms, sys: 2.01 ms, total: 9.5 ms
Wall time: 5.92 s


In [119]:
%%time
load_nodes(gds, product_df, 'productCode', 'Product')

======  loading Product nodes  ======
staging 8,044 records
Loaded 8,044 of 8,044 nodes
CPU times: user 181 ms, sys: 8.21 ms, total: 189 ms
Wall time: 15.2 s


In [120]:
%%time
load_nodes(gds, article_df.drop(columns=['productCode', 'departmentNo']), 'articleId', 'Article')

======  loading Article nodes  ======
staging 13,351 records
Loaded 10,000 of 13,351 nodes
Loaded 13,351 of 13,351 nodes
CPU times: user 264 ms, sys: 10.8 ms, total: 275 ms
Wall time: 10.9 s


In [121]:
%%time
load_nodes(gds, customer_df, 'customerId', 'Customer')

======  loading Customer nodes  ======
staging 1,000 records
Loaded 1,000 of 1,000 nodes
CPU times: user 22.1 ms, sys: 2.77 ms, total: 24.9 ms
Wall time: 2.78 s


### Load Relationships

In [122]:
%%time
load_rels(gds, article_df[['articleId', 'departmentNo']], source_target_labels=('Article', 'Department'),
          source_node_key='articleId', target_node_key='departmentNo',
          rel_type='FROM_DEPARTMENT')

======  loading FROM_DEPARTMENT relationships  ======
staging 13,351 records
Loaded 10,000 of 13,351 relationships
Loaded 13,351 of 13,351 relationships
CPU times: user 81.6 ms, sys: 4.18 ms, total: 85.8 ms
Wall time: 11.5 s


In [123]:
%%time
load_rels(gds, article_df[['articleId', 'productCode']], source_target_labels=('Article', 'Product'),
          source_node_key='articleId',target_node_key='productCode',
          rel_type='VARIANT_OF')

======  loading VARIANT_OF relationships  ======
staging 13,351 records
Loaded 10,000 of 13,351 relationships
Loaded 13,351 of 13,351 relationships
CPU times: user 92.2 ms, sys: 3.94 ms, total: 96.1 ms
Wall time: 7.57 s


In [124]:
%%time
load_rels(gds, transaction_df, source_target_labels=('Customer', 'Article'),
          source_node_key='customerId', target_node_key='articleId',
          rel_type='PURCHASED')

======  loading PURCHASED relationships  ======
staging 23,199 records
Loaded 10,000 of 23,199 relationships
Loaded 20,000 of 23,199 relationships
Loaded 23,199 of 23,199 relationships
CPU times: user 382 ms, sys: 12.4 ms, total: 394 ms
Wall time: 16.5 s


### Convert Transaction Dates

In [125]:
gds.run_cypher('''
MATCH (:Customer)-[r:PURCHASED]->()
SET r.tDat = date(r.tDat)
''')

Empty DataFrame
Columns: []
Index: []

## Vector Search
In this Section We will build Text Embeddings of Product and demonstrate how to leverage the Neo4j vector index for vector search.

### Creating Text Embeddings

In [126]:
def load_embedding_model(embedding_model_name: str):
    if embedding_model_name == "openai":
        embeddings = OpenAIEmbeddings()
        dimension = 1536
        print("Embedding Model: openai")
    elif embedding_model_name == "aws":
        embeddings = BedrockEmbeddings()
        dimension = 1536
        print("Embedding Model: aws")
    else:
        embeddings = SentenceTransformerEmbeddings(
            model_name="all-MiniLM-L6-v2", cache_folder="/embedding_model")
        print("Embedding Model: sentence transformer")
        dimension = 384
    return embeddings, dimension

In [127]:
embedding_model, dimension = load_embedding_model(EMBEDDING_MODEL)

Embedding Model: openai


In [133]:
product_emb_df = product_df[['productCode', 'prodName', 'productTypeName', 'productGroupName', 'garmentGroupName', 'detailDesc']]
product_emb_df = product_emb_df[product_emb_df.detailDesc.notnull()]

In [134]:
def create_doc(row):
    return f'''
##Product
Name: {row.prodName}
Type: {row.productTypeName}
Group: {row.productGroupName}
Garment Type: {row.garmentGroupName}
Description: {row.detailDesc}
'''

product_emb_df['text'] = product_emb_df.apply(create_doc, axis=1)
product_emb_df = product_emb_df.drop(columns=['prodName', 'productTypeName', 'productGroupName', 'garmentGroupName', 'detailDesc'])
product_emb_df

productCode                                               text
0          108775  \n##Product\nName: Strap top\nType: Vest top\n...
1          110065  \n##Product\nName: OP T-shirt (Idro)\nType: Br...
2          111565  \n##Product\nName: 20 den 1p Stockings\nType: ...
3          111586  \n##Product\nName: Shape Up 30 den 1p Tights\n...
4          111593  \n##Product\nName: Support 40 den 1p Tights\nT...
...           ...                                                ...
8039       936862  \n##Product\nName: EDC Marla dress\nType: Dres...
8040       936979  \n##Product\nName: Class Filippa Necklace\nTyp...
8041       937138  \n##Product\nName: Flirty Albin bracelet pk\nT...
8042       942187  \n##Product\nName: ED Sasha tee\nType: T-shirt...
8043       952938  \n##Product\nName: Elton top\nType: Top\nGroup...

[8018 rows x 2 columns]

In [137]:
%%time

count = 0
embeddings = []
for docs in chunks(product_emb_df.text, n=500):
    count += len(docs)
    print(f'Embedded {count} of {product_emb_df.shape[0]}')
    embeddings.extend(embedding_model.embed_documents(docs))

Embedded 500 of 8018
Embedded 1000 of 8018
Embedded 1500 of 8018
Embedded 2000 of 8018
Embedded 2500 of 8018
Embedded 3000 of 8018
Embedded 3500 of 8018
Embedded 4000 of 8018
Embedded 4500 of 8018
Embedded 5000 of 8018
Embedded 5500 of 8018
Embedded 6000 of 8018
Embedded 6500 of 8018
Embedded 7000 of 8018
Embedded 7500 of 8018
Embedded 8000 of 8018
Embedded 8018 of 8018
CPU times: user 1.81 s, sys: 206 ms, total: 2.02 s
Wall time: 25.8 s


In [139]:
product_emb_df['textEmbedding'] = embeddings
product_emb_df

productCode                                               text  \
0          108775  \n##Product\nName: Strap top\nType: Vest top\n...   
1          110065  \n##Product\nName: OP T-shirt (Idro)\nType: Br...   
2          111565  \n##Product\nName: 20 den 1p Stockings\nType: ...   
3          111586  \n##Product\nName: Shape Up 30 den 1p Tights\n...   
4          111593  \n##Product\nName: Support 40 den 1p Tights\nT...   
...           ...                                                ...   
8039       936862  \n##Product\nName: EDC Marla dress\nType: Dres...   
8040       936979  \n##Product\nName: Class Filippa Necklace\nTyp...   
8041       937138  \n##Product\nName: Flirty Albin bracelet pk\nT...   
8042       942187  \n##Product\nName: ED Sasha tee\nType: T-shirt...   
8043       952938  \n##Product\nName: Elton top\nType: Top\nGroup...   

                                          textEmbedding  
0     [-0.03165835786785922, 0.010735359633722455, -...  
1     [-0.012618998246342304, 0.006922205543577324, ...  
2     [-0.004641780213279706, -0.0002350378369905564...  
3     [-0.004515952400410634, -0.00448439686023379, ...  
4     [-0.011169078802241895, 0.002781850762048061, ...  
...                                                 ...  
8039  [-0.02878346256636124, 0.01268400503673369, -0...  
8040  [-0.016470516922509736, 0.01204499569297766, -...  
8041  [-0.032225362565817726, 0.02832645888555731, -...  
8042  [-0.008373181850647395, 0.007136464695464776, ...  
8043  [-0.024706963217868964, -0.0001193681752402107...  

[8018 rows x 3 columns]

#### Create Vector Property

In [140]:
records = product_emb_df[['productCode', 'textEmbedding']].to_dict('records')
print(f'======  loading Product text embeddings ======')
total = len(records)
print(f'staging {total:,} records')
cumulative_count = 0
for recs in chunks(records, n=100):
    res = gds.run_cypher('''
    UNWIND $recs AS rec
    MATCH(n:Product {productCode: rec.productCode})
    CALL db.create.setNodeVectorProperty(n, "textEmbedding", rec.textEmbedding)
    RETURN count(n) AS propertySetCount
    ''', params={'recs': recs})
    cumulative_count += res.iloc[0, 0]
    print(f'Set {cumulative_count:,} of {total:,} text embeddings')

======  loading Product text embeddings ======
staging 8,018 records
Set 100 of 8,018 text embeddings
Set 200 of 8,018 text embeddings
Set 300 of 8,018 text embeddings
Set 400 of 8,018 text embeddings
Set 500 of 8,018 text embeddings
Set 600 of 8,018 text embeddings
Set 700 of 8,018 text embeddings
Set 800 of 8,018 text embeddings
Set 900 of 8,018 text embeddings
Set 1,000 of 8,018 text embeddings
Set 1,100 of 8,018 text embeddings
Set 1,200 of 8,018 text embeddings
Set 1,300 of 8,018 text embeddings
Set 1,400 of 8,018 text embeddings
Set 1,500 of 8,018 text embeddings
Set 1,600 of 8,018 text embeddings
Set 1,700 of 8,018 text embeddings
Set 1,800 of 8,018 text embeddings
Set 1,900 of 8,018 text embeddings
Set 2,000 of 8,018 text embeddings
Set 2,100 of 8,018 text embeddings
Set 2,200 of 8,018 text embeddings
Set 2,300 of 8,018 text embeddings
Set 2,400 of 8,018 text embeddings
Set 2,500 of 8,018 text embeddings
Set 2,600 of 8,018 text embeddings
Set 2,700 of 8,018 text embeddings
Set 

#### Create Vector Index

In [141]:
%%time

gds.run_cypher(f'CALL db.index.vector.createNodeIndex("product-text-embeddings", "Product", "textEmbedding", {dimension}, "cosine")')

# wait for full index creation (timeout after 300 seconds)
gds.run_cypher('CALL db.awaitIndex("product-text-embeddings", 300)')

CPU times: user 5.43 ms, sys: 2.86 ms, total: 8.29 ms
Wall time: 1min 7s


Empty DataFrame
Columns: []
Index: []

#### Create Combined Text Property
This to mirror what was used in the text embedding above.  Creating this will help with retrieval later.

In [301]:
gds.run_cypher("""
    MATCH(p:Product)
    SET p.text = '##Product\n' +
        'Name: ' + p.prodName + '\n' +
        'Type: ' + p.productTypeName + '\n' +
        'Group: ' + p.productGroupName + '\n' +
        'Garment Type: ' + p.garmentGroupName + '\n' +
        'Description: ' + p.detailDesc
    RETURN count(p) AS propertySetCount
    """)

propertySetCount
0              8044

### Vector Search Using Cypher

In [142]:
#search_prompt = 'denim jeans, loose fit, high-waist'
search_prompt = 'Oversized Sweaters'

In [143]:
query_vector = embedding_model.embed_query(search_prompt)
print(f'query vector length: {len(query_vector)}')
print(f'query vector sample: {query_vector[:10]}')

query vector length: 1536
query vector sample: [-0.023104330485734847, -0.013533096737628139, 0.0017341322934734697, -0.033839277865887946, -0.024241894442575403, 0.011094523575023529, -0.006240261242417779, -0.0017504765389690473, 0.005606101350692616, -0.024660309734965396]


In [170]:
gds.run_cypher('''
CALL db.index.vector.queryNodes("product-text-embeddings", 10, $queryVector)
YIELD node AS product, score
RETURN product.productCode AS productCode,
    product.text AS text,
    score
''', params={'queryVector': query_vector})

productCode                                               text     score
0       842001  \n##Product\nName: Betsy Oversized\nType: Swea...  0.942261
1       817392  \n##Product\nName: Japp oversize sweater\nType...  0.939759
2       709418  \n##Product\nName: DIV Anni oversize hood\nTyp...  0.928798
3       860833  \n##Product\nName: Runar sweater\nType: Sweate...  0.926939
4       893141  \n##Product\nName: Sandy\nType: Sweater\nGroup...  0.925745
5       812167  \n##Product\nName: Macy\nType: Sweater\nGroup:...  0.925685
6       690623  \n##Product\nName: Simba\nType: Sweater\nGroup...  0.924674
7       557247  \n##Product\nName: Petar Sweater(1)\nType: Swe...  0.923877
8       687934  \n##Product\nName: Sister off shoulder\nType: ...  0.923150
9       594834  \n##Product\nName: Dolly hood\nType: Sweater\n...  0.923108

### Vector Search Using Langchain

We can also do this with langchain which is a recommended approach going forward.  To do this we use the Neo4jVector class and call the method to sert it up from an existing index in the graph.

In [43]:
from langchain.vectorstores.neo4j_vector import Neo4jVector

In [145]:
kg_vector_search = Neo4jVector.from_existing_index(
    embedding=embedding_model,
    url=NEO4J_URI,
    username=NEO4J_USERNAME,
    password=NEO4J_PASSWORD,
    index_name='product-text-embeddings')

In [146]:
res = kg_vector_search.similarity_search(search_prompt, k=10)
res

[Document(page_content='\n##Product\nName: Betsy Oversized\nType: Sweater\nGroup: Garment Upper body\nGarment Type: Knitwear\nDescription: Oversized, V-neck jumper in a soft, loose knit containing some wool and alpaca wool. Dropped shoulders, long, wide sleeves, wide ribbing around the neckline, cuffs and hem, and slits in the sides.\n', metadata={'prodName': 'Betsy Oversized', 'garmentGroupName': 'Knitwear', 'garmentGroupNo': 1003, 'productCode': 842001, 'productTypeName': 'Sweater', 'productTypeNo': 252, 'detailDesc': 'Oversized, V-neck jumper in a soft, loose knit containing some wool and alpaca wool. Dropped shoulders, long, wide sleeves, wide ribbing around the neckline, cuffs and hem, and slits in the sides.', 'productGroupName': 'Garment Upper body'}),
 Document(page_content='\n##Product\nName: Japp oversize sweater\nType: Sweater\nGroup: Garment Upper body\nGarment Type: Jersey Basic\nDescription: Relaxed-fit top in sweatshirt fabric with a ribbed turtle neck, dropped shoulders

In [147]:
# Visualize as a dataframe
pd.DataFrame([{'document': d.page_content} for d in res])

document
0  \n##Product\nName: Betsy Oversized\nType: Swea...
1  \n##Product\nName: Japp oversize sweater\nType...
2  \n##Product\nName: DIV Anni oversize hood\nTyp...
3  \n##Product\nName: Runar sweater\nType: Sweate...
4  \n##Product\nName: Sandy\nType: Sweater\nGroup...
5  \n##Product\nName: Macy\nType: Sweater\nGroup:...
6  \n##Product\nName: Simba\nType: Sweater\nGroup...
7  \n##Product\nName: Petar Sweater(1)\nType: Swe...
8  \n##Product\nName: Sister off shoulder\nType: ...
9  \n##Product\nName: Dolly hood\nType: Sweater\n...

### Try Yourself

In [176]:
res = kg_vector_search.similarity_search('type your prompt here!', k=10)
pd.DataFrame([{'document': d.page_content} for d in res])

## Semantic Search with Context
Using Explicit Relationships in EN terprise data


Above we see how you can use the vector index to find semantic similar products in user searches.  but there is a rich graph full of other information in it. Lets leverage our knowledge graph to make this better

An important piece of information expressed in this graph, but not directly in the documents, is customer purchasing behavior.  We can use A Cypher Query to make recommendations without any document behavior. this is similar to collaborative filtering but generalized to purchase history (not necessarily rating based)

#### Example Purchase History

Consider the below customer

In [171]:
CUSTOMER_ID = "daae10780ecd14990ea190a1e9917da33fe96cd8cfa5e80b67b4600171aa77e0"
print('Customer Purchase History')
gds.run_cypher('''
    MATCH(c:Customer {customerId: $customerId})-[:PURCHASED]->(:Article)
    -[:VARIANT_OF]->(p:Product)
    RETURN p.productCode AS productCode,
        p.prodName AS prodName,
        p.productTypeName AS productTypeName,
        p.garmentGroupName AS garmentGroupName,
        p.detailDesc AS detailDesc,
        count(*) AS purchaseCount
    ORDER BY purchaseCount DESC
''', params={'customerId': CUSTOMER_ID})

Customer Purchase History


productCode                     prodName  productTypeName  \
0        569974         DONT USE ROLAND HOOD           Hoodie   
1        557247             Petar Sweater(1)          Sweater   
2        733027                         Tove              Top   
3        753724                     Rosemary            Dress   
4        687016                   DORIS CREW          Sweater   
5        691072             JEKYL SWEATSHIRT          Sweater   
6        244267                  Silver lake          Sweater   
7        606711               Rylee flatform   Heeled sandals   
8        660519            Haven back detail              Bra   
9        585480         Adore strapless push              Bra   
10       662328                     Survivor           Blouse   
11       688537  Simple as that Cheeky Tanga  Swimwear bottom   
12       731142             Lead Superskinny         Trousers   
13       640129                Eden SP Andes              Bra   
14       642498       Bubble Bum Bandeau (1)       Bikini top   
15       656401               PASTRY SWEATER          Sweater   
16       511924             Leona Push Mirny              Bra   
17       620425               Karin headband         Hairband   
18       713577                 Malte r-neck          Sweater   
19       557246                   Hood W Zip           Hoodie   
20       598806                    Dixie tee          T-shirt   
21       682848    Skinny  RW Ankle Milo Zip         Trousers   
22       752193                        Banks           Hoodie   

     garmentGroupName                                         detailDesc  \
0        Jersey Basic  Top in sweatshirt fabric with a lined drawstri...   
1        Jersey Basic  Oversized top in sturdy sweatshirt fabric with...   
2        Jersey Fancy  Short top in soft cotton jersey with a round n...   
3      Dresses Ladies  Short dress in woven fabric with 3/4-length sl...   
4        Jersey Fancy  Top in sweatshirt fabric with a motif on the f...   
5        Jersey Basic  Top in sweatshirt fabric with long raglan slee...   
6            Knitwear  Purl-knit jumper in a cotton blend with a slig...   
7               Shoes  Sandals with imitation suede straps, an elasti...   
8   Under-, Nightwear  Push-up bra in lace and mesh with underwired, ...   
9   Under-, Nightwear  Strapless balconette bra in microfibre with un...   
10            Blouses  Straight-cut blouse in a crêpe weave with a co...   
11           Swimwear  Fully lined bikini bottoms with a mid waist an...   
12           Trousers  Chinos in stretch twill with a zip fly and but...   
13  Under-, Nightwear  Super push-up bra in lace with underwired, thi...   
14           Swimwear  Fully lined bandeau bikini top with padded cup...   
15           Knitwear  Jumper in soft, textured-knit cotton with long...   
16  Under-, Nightwear  Push-up bra in lace and mesh with underwired, ...   
17        Accessories  Wide hairband in cotton jersey with a twisted ...   
18           Knitwear  Jumper in soft, patterned, fine-knit cotton wi...   
19       Jersey Basic  Long-sleeved jacket in sweatshirt fabric with ...   
20       Jersey Fancy  Short top in soft cotton jersey with short sle...   
21     Trousers Denim  5-pocket, ankle-length jeans in washed stretch...   
22       Jersey Basic  Long-sleeved top in sweatshirt fabric made fro...   

    purchaseCount  
0               2  
1               2  
2               1  
3               1  
4               1  
5               1  
6               1  
7               1  
8               1  
9               1  
10              1  
11              1  
12              1  
13              1  
14              1  
15              1  
16              1  
17              1  
18              1  
19              1  
20              1  
21              1  
22              1

#### Graph Patterns For Retrieval Query

In [102]:
# This is the example Pattern we can use to predict likely customer preferences based on collaborative behavior
gds.run_cypher('''
    MATCH(c:Customer {customerId: $customerId})-[:PURCHASED]->(:Article)
    <-[:PURCHASED]-(:Customer)-[:PURCHASED]->(:Article)
    -[:VARIANT_OF]->(p:Product)
    RETURN p.productCode AS productCode,
        p.prodName AS prodName,
        p.productTypeName AS productTypeName,
        p.garmentGroupName AS garmentGroupName,
        p.detailDesc AS detailDesc,
        count(*) AS score
    ORDER BY score DESC LIMIT 10
''', params={'customerId': CUSTOMER_ID})

productCode                     prodName  productTypeName garmentGroupName  \
0       685816         RONNY REG RN T-SHIRT          T-shirt     Jersey Basic   
1       599580       Timeless Midrise Brief  Swimwear bottom         Swimwear   
2       684209  Simple as That Triangle Top       Bikini top         Swimwear   
3       688537  Simple as that Cheeky Tanga  Swimwear bottom         Swimwear   
4       778064             Claudine t-shirt          T-shirt     Jersey Basic   
5       656719     Serpente HW slim trouser         Trousers         Trousers   
6       615141                       Juanos              Top     Jersey Fancy   
7       776237      Shake it in Balconette.       Bikini top         Swimwear   
8       685813             PETAR SWEATSHIRT          Sweater     Jersey Basic   
9       685814                  RICHIE HOOD           Hoodie     Jersey Basic   

                                          detailDesc  score  
0        Round-necked T-shirt in soft cotton jersey.     17  
1  Fully lined bikini bottoms with a mid waist an...     16  
2  Lined, non-wired, triangle bikini top with a w...     13  
3  Fully lined bikini bottoms with a mid waist an...     12  
4  Fitted top in soft organic cotton jersey with ...      9  
5  Tailored trousers in a stretch weave with two ...      6  
6  Long-sleeved, fitted top in ribbed jersey with...      6  
7  Lined balconette bikini top with underwired, p...      6  
8  Top in soft sweatshirt fabric. Slightly looser...      6  
9  Hoodie in sweatshirt fabric made from a cotton...      5

In [173]:
# This is the example Pattern we can use to predict likely customer preferences based on collaborative behavior
kg_personalized_search = Neo4jVector.from_existing_index(
    embedding=embedding_model,
    url=NEO4J_URI,
    username=NEO4J_USERNAME,
    password=NEO4J_PASSWORD,
    index_name='product-text-embeddings',
    retrieval_query=f"""
    WITH node AS product, score AS searchScore

    OPTIONAL MATCH(product)<-[:VARIANT_OF]-(:Article)<-[:PURCHASED]-(:Customer)
    -[:PURCHASED]->(a:Article)<-[:PURCHASED]-(:Customer {{customerId: '{CUSTOMER_ID}'}})

    WITH count(a) AS purchaseScore, product.text AS text, searchScore, product.productCode AS productCode
    RETURN text,
        (1+purchaseScore)*searchScore AS score,
        {{productCode: productCode, purchaseScore:purchaseScore, searchScore:searchScore}} AS metadata
    ORDER BY purchaseScore DESC, searchScore DESC LIMIT 15
    """)

In [174]:
res = kg_personalized_search.similarity_search(search_prompt, k=100)

# Visualize as a dataframe
pd.DataFrame([{'productCode': d.metadata['productCode'],
               'document': d.page_content,
               'searchScore': d.metadata['searchScore'],
               'purchaseScore': d.metadata['purchaseScore']} for d in res])

productCode                                           document  \
0        677930  \n##Product\nName: Queen Sweater\nType: Sweate...   
1        516712  \n##Product\nName: Jess oversize LS\nType: Top...   
2        669682  \n##Product\nName: Irma sweater\nType: Sweater...   
3        640755  \n##Product\nName: Allen Sweater\nType: Sweate...   
4        687948  \n##Product\nName: Annie Oversized Hood\nType:...   
5        709991  \n##Product\nName: SISTER OL\nType: Sweater\nG...   
6        687856  \n##Product\nName: Jacket Oversize\nType: Jack...   
7        686265  \n##Product\nName: Family Crew Ladies\nType: S...   
8        845520  \n##Product\nName: Dolls Printed\nType: Sweate...   
9        674826  \n##Product\nName: Fine knit\nType: Sweater\nG...   
10       782451  \n##Product\nName: Pickles Velour Sweater\nTyp...   
11       547300  \n##Product\nName: Harley Sweater\nType: Sweat...   
12       675408  \n##Product\nName: Mother\nType: Sweater\nGrou...   
13       842001  \n##Product\nName: Betsy Oversized\nType: Swea...   
14       817392  \n##Product\nName: Japp oversize sweater\nType...   

    searchScore  purchaseScore  
0      0.918759              4  
1      0.918976              2  
2      0.917643              2  
3      0.922795              1  
4      0.921786              1  
5      0.921149              1  
6      0.919922              1  
7      0.918640              1  
8      0.917355              1  
9      0.917115              1  
10     0.916920              1  
11     0.916153              1  
12     0.916103              1  
13     0.942261              0  
14     0.939759              0

In [172]:
# OPTIONAL version without Langchain
# gds.run_cypher('''
# CALL db.index.vector.queryNodes("product-text-embeddings", 100, $queryVector)
# YIELD node AS product, score AS searchScore
#
# OPTIONAL MATCH(product)<-[:VARIANT_OF]-(:Article)<-[:PURCHASED]-(:Customer)
# -[:PURCHASED]->(a:Article)<-[:PURCHASED]-(:Customer {customerId: $customerId})
#
# WITH product.text AS text, count(a) AS purchaseScore, searchScore, product.productCode AS productCode
# RETURN text, (1+purchaseScore)*searchScore AS score, productCode, purchaseScore, searchScore
# ORDER BY purchaseScore DESC, searchScore DESC LIMIT 15
# ''', params={'queryVector': embedding_model.embed_query("Oversized Sweater"), 'customerId': CUSTOMER_ID})

## KG Powered Inference for AI

We saw before how could use graph pattern matching to personalize search and make it more relevant.

Graph pattern matching is very power and can work well in a lot of scenarios.

In addition to this, we also have Graph Data Science, which can allow as to enrich the current Knowledge graph with machine learning, that can
1. Provide addition information to improve relevancy of search results at scale
2. Provide additional inferences to GenAI

We will show an example of how this works using Node Embedding and K-Nearest Neighbor algorithms



### Graph Embedding

In [269]:
pd.set_option('display.max_rows', 20)
pd.set_option('display.max_colwidth', 500)
pd.set_option('display.width', 0)

In [178]:
def clear_all_graphs():
    g_names = gds.graph.list().graphName.tolist()
    for g_name in g_names:
        g = gds.graph.get(g_name)
        g.drop()

#### Clear Past Analysis (If rerunning this Notebook)

In [233]:
clear_all_graphs()

In [264]:
gds.run_cypher('''
    MATCH(:Article)-[r:CUSTOMERS_ALSO_LIKE]->()
    CALL {
        WITH r
        DELETE r
    } IN TRANSACTIONS OF 1000 ROWS
    ''')

Empty DataFrame
Columns: []
Index: []

#### Apply Fast Random Projection Node Embedding

First, apply a graph projection to structure the portion of the graph we need in an optimized in-memory format for graph ML.

In [234]:
%%time

# graph projection
gds.run_cypher('''
   MATCH (a1:Article)<-[:PURCHASED]-(:Customer)-[:PURCHASED]->(a2:Article)
   WITH gds.graph.project("proj", a1, a2,
       {sourceNodeLabels: labels(a1),
       targetNodeLabels: labels(a2),
       relationshipType: "COPURCHASE"}) AS g
   RETURN g.graphName
   ''')

g = gds.graph.get("proj")

CPU times: user 6.78 ms, sys: 2.24 ms, total: 9.01 ms
Wall time: 6.57 s


Next, we will generate node embeddings for similarity calculation.  In this case, we will use FastRP (Fast Random Projection) which is a fast, scalable, and robust embedding algorithm. FastRP calculates embeddings using probabilistic sampling and linear algebra.

In [235]:
%%time
# embeddings (writing back Article embeddings in case we want to introspect later)
gds.fastRP.mutate(g, mutateProperty='embedding', embeddingDimension=128, randomSeed=7474, concurrency=4, iterationWeights=[0.0, 1.0, 1.0])
gds.graph.writeNodeProperties(g, ['embedding'], ['Article'])

FastRP:   0%|          | 0/100 [00:00<?, ?%/s]

CPU times: user 25.9 ms, sys: 9.17 ms, total: 35.1 ms
Wall time: 3.06 s


writeMillis                 1365
graphName                   proj
nodeProperties       [embedding]
propertiesWritten          13288
Name: 0, dtype: object

#### Explore Node Embeddings

In [271]:
graph_emb_df = gds.run_cypher('''
MATCH (p:Product)<-[:VARIANT_OF]-(a:Article)-[:FROM_DEPARTMENT]-(d)
RETURN a.articleId AS articleId,
    p.prodName AS productName,
    p.productTypeName AS productTypeName,
    d.departmentName AS departmentName,
    d.sectionName AS sectionName,
    p.detailDesc AS detailDesc,
    a.embedding AS embedding
''')

In [254]:
graph_emb_df[:3]

articleId        productName productTypeName  departmentName  \
0  108775015          Strap top        Vest top    Jersey Basic   
1  108775044          Strap top        Vest top    Jersey Basic   
2  110065001  OP T-shirt (Idro)             Bra  Clean Lingerie   

              sectionName  \
0  Womens Everyday Basics   
1  Womens Everyday Basics   
2         Womens Lingerie   

                                                                                                                                                                                                                                         detailDesc  \
0                                                                                                                                                                                                           Jersey top with narrow shoulder straps.   
1                                                                                                                                                                                                           Jersey top with narrow shoulder straps.   
2  Microfibre T-shirt bra with underwired, moulded, lightly padded cups that shape the bust and provide good support. Narrow adjustable shoulder straps and a narrow hook-and-eye fastening at the back. Without visible seams for greater comfort.   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                             embedding  
0  [0.19398054480552673, 0.11711762100458145, 0.06496361643075943, -0.11650612205266953, -0.03101484291255474, -0.24193497002124786, -0.12506884336471558, -0.00604782160371542, 0.0013523102970793843, -0.13710147142410278, 0.05550107732415199, -0.05964566022157669, -0.1769135296344757, 0.06761161237955093, -0.052474625408649445, 0.10341720283031464, -0.1007346361875534, -0.09389939904212952, -0.17400702834129333, -0.10375046730041504, 0.17132458090782166, 0.03985965624451637, -0.0669625177979469...  
1  [0.2109856903553009, -0.06980044394731522, 0.11304987967014313, -0.2276107370853424, 0.09551478177309036, -0.2264857292175293, -0.09112216532230377, -0.1393982470035553, 0.014033649116754532, 0.07845285534858704, -0.010077900253236294, 0.09189127385616302, 0.13155078887939453, -0.13943827152252197, 0.05554193630814552, 0.32880812883377075, -0.1351064145565033, -0.17323368787765503, -0.04095638915896416, -0.1350538730621338, 0.24013163149356842, 0.11544935405254364, 0.056026753038167953, 0.05...  
2  [-0.08901850879192352, 0.006348952651023865, -0.17539185285568237, 0.24354404211044312, 0.1677209734916687, -0.02687895856797695, 0.0559389628469944, -0.40726393461227417, -0.06479780375957489, -0.1261589080095291, 0.1922130286693573, -0.03428041934967041, 0.2290419340133667, 0.03030058741569519, 0.038854047656059265, 0.36568713188171387, 0.3510403633117676, -0.07354778051376343, -0.13295245170593262, 0.022946149110794067, -0.05766115337610245, 0.16961818933486938, -0.012528732419013977, 0.1...

In [255]:
from sklearn.manifold import TSNE

df = graph_emb_df.copy()
filtered_node_df = df[df.embedding.apply(lambda x: np.count_nonzero(x) > 0)].reset_index(drop=True)
# instantiate the TSNE model
tsne = TSNE(n_components=2, random_state=7474, init='random', learning_rate="auto")
# Use the TSNE model to fit and output a 2-d representation
E = tsne.fit_transform(np.stack(filtered_node_df['embedding'], axis=0))

coord_df = pd.concat([filtered_node_df, pd.DataFrame(E, columns=['x', 'y'])], axis=1)
coord_df

articleId                productName   productTypeName  \
0      108775015                  Strap top          Vest top   
1      108775044                  Strap top          Vest top   
2      110065001          OP T-shirt (Idro)               Bra   
3      111565001        20 den 1p Stockings  Underwear Tights   
4      111586001  Shape Up 30 den 1p Tights   Leggings/Tights   
...          ...                        ...               ...   
13346  936862001            EDC Marla dress             Dress   
13347  936979001     Class Filippa Necklace          Necklace   
13348  937138001   Flirty Albin bracelet pk          Bracelet   
13349  942187001               ED Sasha tee           T-shirt   
13350  952938001                  Elton top               Top   

           departmentName                     sectionName  \
0            Jersey Basic          Womens Everyday Basics   
1            Jersey Basic          Womens Everyday Basics   
2          Clean Lingerie                 Womens Lingerie   
3            Tights basic  Womens Nightwear, Socks & Tigh   
4            Tights basic  Womens Nightwear, Socks & Tigh   
...                   ...                             ...   
13346           Campaigns      Womens Everyday Collection   
13347           Jewellery        Womens Small accessories   
13348  Jewellery Extended        Womens Small accessories   
13349              Jersey                            H&M+   
13350              Jersey                    Womens Trend   

                                                                                                                                                                                                                                                                                                                                             detailDesc  \
0                                                                                                                                                                                                                                                                                                               Jersey top with narrow shoulder straps.   
1                                                                                                                                                                                                                                                                                                               Jersey top with narrow shoulder straps.   
2                                                                                                      Microfibre T-shirt bra with underwired, moulded, lightly padded cups that shape the bust and provide good support. Narrow adjustable shoulder straps and a narrow hook-and-eye fastening at the back. Without visible seams for greater comfort.   
3                                                                                                                                                                                                                                             Semi shiny nylon stockings with a wide, reinforced trim at the top. Use with a suspender belt. 20 denier.   
4                                                                                                                                                                                                                                                     Tights with built-in support to lift the bottom. Black in 30 denier and light amber in 15 denier.   
...                                                                                                                                                                                                                                                                                                                                                 ...   
13346  Calf-length dress in a patterned Tencel™ lyocell weave wi

In [257]:
import altair as alt
from sklearn.manifold import TSNE

alt.data_transformers.enable("vegafusion")
chart = alt.Chart(coord_df).mark_circle(size=60).encode(
    x='x',
    y='y',
    tooltip=['productName', 'productTypeName', 'departmentName' , 'sectionName', 'detailDesc']
).properties(title="Article Embedding (2D Representation)", width=750, height=700)

chart = chart.configure_axis(titleFontSize=20)
chart.configure_legend(labelFontSize = 20)

alt.Chart(...)

### K-Nearest Neighbors (KNN) Relationships

Finally, we can do our similarity inference with K-Nearest Neighbor (KNN) and write back to the graph.
We will use a slightly low cutoff of 0.75 similarity score to extend the result size for exploration.  We can provide a higher cutoff at query time if needed.

In [266]:
%%time
# KNN
_ = gds.knn.write(g, nodeProperties=['embedding'], nodeLabels=['Article'],
                  writeRelationshipType='CUSTOMERS_ALSO_LIKE', writeProperty='score',
                  sampleRate=1.0, initialSampler='randomWalk', concurrency=1, similarityCutoff=0.75, randomSeed=7474)
_

Knn:   0%|          | 0/100 [00:00<?, ?%/s]

CPU times: user 150 ms, sys: 36.1 ms, total: 186 ms
Wall time: 19.5 s


ranIterations                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              6
didConverge                                                                                                                                                                                                                                                                                                                                                                                                                                                                                

In [267]:
# clear graph projection once done
g.drop()

graphName                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                     proj
database                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                     neo4j
me

### Tailored Recommendations from Search

Let's construct a KG store to retrieve recommendations based on search

In [349]:
kg_search_recommendations = Neo4jVector.from_existing_index(
    embedding=embedding_model,
    url=NEO4J_URI,
    username=NEO4J_USERNAME,
    password=NEO4J_PASSWORD,
    index_name='product-text-embeddings',
    retrieval_query="""
    WITH node as searchProduct, score as searchScore
    MATCH(searchProduct)<-[:VARIANT_OF]-(:Article)-[r:CUSTOMERS_ALSO_LIKE]->(:Article)-[:VARIANT_OF]-(product)
    WITH  product, searchScore, sum(r.score*searchScore) AS recommenderScore
    RETURN product.text AS text,
    recommenderScore AS score,
    {productCode: product.productCode, productType: product.productTypeName, recommenderScore:recommenderScore} AS metadata
    ORDER BY score DESC LIMIT 100
    """
)

In [350]:
res = kg_search_recommendations.similarity_search(search_prompt, k=100)

# Visualize as a dataframe
pd.DataFrame([{'productCode': d.metadata['productCode'],
               'productType':d.metadata['productType'],
               'document': d.page_content,
               'recommenderScore': d.metadata['recommenderScore']} for d in res])

productCode productType  \
0        863561         Bra   
1        658030    Trousers   
2        707135     Sweater   
3        903084      Blouse   
4        672032       Scarf   
..          ...         ...   
95       738899       Dress   
96       906100     Sweater   
97       801068    Cardigan   
98       687720    Trousers   
99       781135    Trousers   

                                                                                                                                                                                                                                                                                                                                                                  document  \
0   ##Product\nName: Alexis seamless top Rio Opt1\nType: Bra\nGroup: Underwear\nGarment Type: Under-, Nightwear\nDescription: Soft, non-wired bra top in ribbed fabric designed with the minimum number of seams for a seamless, comfortable feel against the skin. Adjustable shoulder straps and padded cups that shape the bust and provide good support. No fasteners.   
1                                                           ##Product\nName: Push Up Jegging L.W\nType: Trousers\nGroup: Garment Lower body\nGarment Type: Trousers Denim\nDescription: 5-pocket jeggings in washed, stretch denim with a low waist, zip fly and button, and skinny legs. Push up – denim with a superstretch function that showcases the body’s physique.   
2                                                                                                                                                                              ##Product\nName: Vivi boatneck\nType: Sweater\nGroup: Garment Upper body\nGarment Type: Knitwear\nDescription: Jumper in a fine-knit viscose blend with a boat neck and 3/4-length sleeves.   
3     ##Product\nName: Alyx blouse\nType: Blouse\nGroup: Garment Upper body\nGarment Type: Blouses\nDescription: Blouse in soft lace made from a cotton blend with a stand-up collar that has gathers all round and an opening with covered buttons at the back of the neck. Long, raglan balloon sleeves with narrow elastication and a frill trim at the cuffs. Unlined.   
4                                                                                                                                                                                                                      ##Product\nName: Inez Knitted Scarf\nType: Scarf\nGroup: Accessories\nGarment Type: Accessories\nDescription: Scarf in a soft knit. Size 50x170 cm.   
..                                                                                                                                                                                                                                                                                                                                                                     ...   
95                                      ##Product\nName: Banoffe\nType: Dress\nGroup: Garment Full body\nGarment Type: Dresses Ladies\nDescription: Calf-length dress in a cotton and viscose weave with embroidery and inset lace trims. Scalloped V-neck, narrow, adjustable shoulder straps, seam with a lace trim at the waist and a concealed zip at the back. Lined.   
96                                                     ##Product\nName: Winslet jumper\nType: Sweater\nGroup: Garment Upper body\nGarment Type: Knitwear\nDescription: Jumper in a soft, rib-knit wool and alpaca blend with a turtle neck, long, wide sleeves that taper at the cuffs, and ribbing at the cuffs and hem. The polyester content of the jumper is recycled.   
97                                                                                                               ##Product\nName: Trudy Cardigan TVP\nType: Cardigan\nGroup: Garment Upper body\nGarment Type: Knitwear\nDescription: Short, fitted cardigan in a fine knit with a V-neck, buttons down the front, long sleeves and overlocked ed

### Personalized Recommendations

N ow lets look at personalized recommendations for a bit.  To keep things simple we will base this just on purchase history, not search, though we could do both if we wanted to (similar to what we did in the above Semantic Search with context section)

First, we will start by creating a Neo4jGraph object which we can then query. This is different from the vec tor based retrievers above

In [289]:
from langchain.graphs import Neo4jGraph

kg = Neo4jGraph(url=NEO4J_URI, username=NEO4J_USERNAME, password=NEO4J_PASSWORD)

In [344]:
res = kg.query('''
    MATCH(:Customer {customerId:$customerId})-[:PURCHASED]->(:Article)
    -[r:CUSTOMERS_ALSO_LIKE]->(:Article)-[:VARIANT_OF]->(product)
    RETURN product.productCode AS productCode,
        product.prodName AS prodName,
        product.productTypeName AS productType,
        product.text AS document,
        sum(r.score) AS recommenderScore
    ORDER BY recommenderScore DESC LIMIT $k
    ''', params={'customerId': CUSTOMER_ID, 'k':15})

#visualize as dataframe. result is list of dict
pd.DataFrame(res)

productCode                   prodName     productType  \
0        731142           Lead Superskinny        Trousers   
1        598806                  Dixie tee         T-shirt   
2        569974       DONT USE ROLAND HOOD          Hoodie   
3        682848  Skinny  RW Ankle Milo Zip        Trousers   
4        656401             PASTRY SWEATER         Sweater   
5        511924           Leona Push Mirny             Bra   
6        660519          Haven back detail             Bra   
7        753724                   Rosemary           Dress   
8        606711             Rylee flatform  Heeled sandals   
9        640129              Eden SP Andes             Bra   
10       752193                      Banks          Hoodie   
11       620425             Karin headband        Hairband   
12       713577               Malte r-neck         Sweater   
13       642498     Bubble Bum Bandeau (1)      Bikini top   
14       557247           Petar Sweater(1)         Sweater   

                                                                                                                                                                                                                                                                                                                                         document  \
0                                                                                                                          ##Product\nName: Lead Superskinny\nType: Trousers\nGroup: Garment Lower body\nGarment Type: Trousers\nDescription: Chinos in stretch twill with a zip fly and button, side pockets, welt back pockets and skinny legs.   
1                                                                                                                    ##Product\nName: Dixie tee\nType: T-shirt\nGroup: Garment Upper body\nGarment Type: Jersey Fancy\nDescription: Short top in soft cotton jersey with short sleeves. Contrasting colour trims around the neckline and sleeves.   
2                                                                                          ##Product\nName: DONT USE ROLAND HOOD\nType: Hoodie\nGroup: Garment Upper body\nGarment Type: Jersey Basic\nDescription: Top in sweatshirt fabric with a lined drawstring hood, kangaroo pocket, long raglan sleeves and ribbing at the cuffs and hem.   
3     ##Product\nName: Skinny  RW Ankle Milo Zip\nType: Trousers\nGroup: Garment Lower body\nGarment Type: Trousers Denim\nDescription: 5-pocket, ankle-length jeans in washed stretch denim with hard-worn details, a regular waist, zip fly and button, and skinny legs with a zip at the hems. The jeans are made partly from recycled cotton.   
4                                                                                                                   ##Product\nName: PASTRY SWEATER\nType: Sweater\nGroup: Garment Upper body\nGarment Type: Knitwear\nDescription: Jumper in soft, textured-knit cotton with long raglan sleeves and ribbing around the neckline, cuffs and hem.   
5      ##Product\nName: Leona Push Mirny\nType: Bra\nGroup: Underwear\nGarment Type: Under-, Nightwear\nDescription: Push-up bra in lace and mesh with underwired, moulded, padded cups for a larger bust and fuller cleavage. Lace racer back, narrow adjustable shoulder straps, a wide mesh strap at the back and metal fastener at the front.   
6   ##Product\nName: Haven back detail\nType: Bra\nGroup: Underwear\nGarment Type: Under-, Nightwear\nDescription: Push-up bra in lace and mesh with underwired, moulded, padded cups for a larger bust and fuller cleavage. Lace racer back, narrow adjustable shoulder straps, a wide mesh strap at the back and a metal fastener at the front.   
7                                                                                                      ##Product\nName: Rosemary\nType: Dress\nGroup: Garment Full body\nGarment Type: Dresses Ladies\nDescription: Short dress in woven fabric with 3/4-length sleeves with an opening and

We could also make it based of the latest purchases.  For example consider the last purchase for the customer

In [345]:
# last two purchases
pd.DataFrame(kg.query('''
    MATCH(:Customer {customerId:$customerId})-[t:PURCHASED]->(:Article)-[:VARIANT_OF]->(product)
    RETURN product.productCode AS productCode,
        product.prodName AS prodName,
        product.productTypeName AS productType,
        product.text AS document,
        t.tDat as purchaseDate
    ORDER BY purchaseDate DESC LIMIT $k
    ''', params={'customerId': CUSTOMER_ID, 'k':1}))

productCode prodName productType  \
0       733027     Tove         Top   

                                                                                                                                                                                                                                       document  \
0  ##Product\nName: Tove\nType: Top\nGroup: Garment Upper body\nGarment Type: Jersey Fancy\nDescription: Short top in soft cotton jersey with a round neckline, short sleeves and a seam at the hem with a decorative knot detail at the front.   

  purchaseDate  
0   2019-08-05

In [346]:
res = kg.query('''
    MATCH(:Customer {customerId:$customerId})-[t:PURCHASED]->(a:Article)
    WITH a, t.tDat as purchaseDate
    ORDER BY purchaseDate DESC LIMIT $lastNPurchases
    MATCH(a)-[r:CUSTOMERS_ALSO_LIKE]->(:Article)-[:VARIANT_OF]->(product)
    RETURN product.productCode AS productCode,
        product.prodName AS prodName,
        product.productTypeName AS productType,
        product.text AS document,
        sum(r.score) AS recommenderScore
    ORDER BY recommenderScore DESC LIMIT $k
    ''', params={'customerId': CUSTOMER_ID, 'lastNPurchases':20, 'k':15})

#visualize as dataframe. result is list of dict
pd.DataFrame(res)

productCode                   prodName     productType  \
0        731142           Lead Superskinny        Trousers   
1        598806                  Dixie tee         T-shirt   
2        569974       DONT USE ROLAND HOOD          Hoodie   
3        682848  Skinny  RW Ankle Milo Zip        Trousers   
4        511924           Leona Push Mirny             Bra   
5        656401             PASTRY SWEATER         Sweater   
6        660519          Haven back detail             Bra   
7        753724                   Rosemary           Dress   
8        620425             Karin headband        Hairband   
9        606711             Rylee flatform  Heeled sandals   
10       752193                      Banks          Hoodie   
11       640129              Eden SP Andes             Bra   
12       713577               Malte r-neck         Sweater   
13       642498     Bubble Bum Bandeau (1)      Bikini top   
14       557247           Petar Sweater(1)         Sweater   

                                                                                                                                                                                                                                                                                                                                         document  \
0                                                                                                                          ##Product\nName: Lead Superskinny\nType: Trousers\nGroup: Garment Lower body\nGarment Type: Trousers\nDescription: Chinos in stretch twill with a zip fly and button, side pockets, welt back pockets and skinny legs.   
1                                                                                                                    ##Product\nName: Dixie tee\nType: T-shirt\nGroup: Garment Upper body\nGarment Type: Jersey Fancy\nDescription: Short top in soft cotton jersey with short sleeves. Contrasting colour trims around the neckline and sleeves.   
2                                                                                          ##Product\nName: DONT USE ROLAND HOOD\nType: Hoodie\nGroup: Garment Upper body\nGarment Type: Jersey Basic\nDescription: Top in sweatshirt fabric with a lined drawstring hood, kangaroo pocket, long raglan sleeves and ribbing at the cuffs and hem.   
3     ##Product\nName: Skinny  RW Ankle Milo Zip\nType: Trousers\nGroup: Garment Lower body\nGarment Type: Trousers Denim\nDescription: 5-pocket, ankle-length jeans in washed stretch denim with hard-worn details, a regular waist, zip fly and button, and skinny legs with a zip at the hems. The jeans are made partly from recycled cotton.   
4      ##Product\nName: Leona Push Mirny\nType: Bra\nGroup: Underwear\nGarment Type: Under-, Nightwear\nDescription: Push-up bra in lace and mesh with underwired, moulded, padded cups for a larger bust and fuller cleavage. Lace racer back, narrow adjustable shoulder straps, a wide mesh strap at the back and metal fastener at the front.   
5                                                                                                                   ##Product\nName: PASTRY SWEATER\nType: Sweater\nGroup: Garment Upper body\nGarment Type: Knitwear\nDescription: Jumper in soft, textured-knit cotton with long raglan sleeves and ribbing around the neckline, cuffs and hem.   
6   ##Product\nName: Haven back detail\nType: Bra\nGroup: Underwear\nGarment Type: Under-, Nightwear\nDescription: Push-up bra in lace and mesh with underwired, moulded, padded cups for a larger bust and fuller cleavage. Lace racer back, narrow adjustable shoulder straps, a wide mesh strap at the back and a metal fastener at the front.   
7                                                                                                      ##Product\nName: Rosemary\nType: Dress\nGroup: Garment Full body\nGarment Type: Dresses Ladies\nDescription: Short dress in woven fabric with 3/4-length sleeves with an opening and

The same could be done with other filters, such as on transaction date.

## LLM For Generating Grounded Content

Let's use an LLM to automatically generate content for targeted marketing campaigns grounded with our knowledge graph using the above tools.
Here is a quick example for generating promotional messages. but you can create all sorts of content with this!

For our first message, let's consider a scenario where a user recently searched for products, but perhaps didn't commit to a purchase yet. We now want to send a message to promote relevant products.

In [347]:
# Import relevant libraries
from langchain.prompts import SystemMessagePromptTemplate, HumanMessagePromptTemplate, ChatPromptTemplate
from langchain.chat_models import ChatOpenAI, BedrockChat
from langchain.schema import StrOutputParser

In [348]:
#load LLM

def load_llm(llm_name: str):
    if llm_name == "gpt-4":
        print("LLM: Using GPT-4")
        return ChatOpenAI(temperature=0, model_name="gpt-4", streaming=True)
    elif llm_name == "gpt-3.5":
        print("LLM: Using GPT-3.5")
        return ChatOpenAI(temperature=0, model_name="gpt-3.5-turbo", streaming=True)
    elif llm_name == "claudev2":
        print("LLM: ClaudeV2")
        return BedrockChat(
            model_id="anthropic.claude-v2",
            model_kwargs={"temperature": 0.0, "max_tokens_to_sample": 1024},
            streaming=True,
        )
    print("LLM: Using GPT-3.5")
    return ChatOpenAI(temperature=0, model_name="gpt-3.5-turbo", streaming=True)


llm = load_llm(LLM)

LLM: Using GPT-3.5


### Create Knowledge Graph Stores for Retrieval
To ground our content Generation we need to define retrievers to pull information from our knowledge graph.  Let's make two stores:
1. Personalized Search Retriever (`kg_personalized_search`): Based on recent customer searches and purchase history, pull relevant products
2. Recommendations retriever (`kg_recommendations`): Based on recent customer searches, what else may we recommend to them?

In [416]:
# This will be a function so we can change per customer id
# We will use a mock URL for our sources in the metadata
def kg_personalized_search_gen(customer_id):
    return Neo4jVector.from_existing_index(
        embedding=embedding_model,
        url=NEO4J_URI,
        username=NEO4J_USERNAME,
        password=NEO4J_PASSWORD,
        index_name='product-text-embeddings',
        retrieval_query=f"""
        WITH node AS product, score AS searchScore

        OPTIONAL MATCH(product)<-[:VARIANT_OF]-(:Article)<-[:PURCHASED]-(:Customer)
        -[:PURCHASED]->(a:Article)<-[:PURCHASED]-(:Customer {{customerId: '{customer_id}'}})
        WITH count(a) AS purchaseScore, product, searchScore
        RETURN product.text + '\nurl: ' + 'https://representative-domain/product/' + product.productCode  AS text,
            (1.0+purchaseScore)*searchScore AS score,
            {{source: 'https://representative-domain/product/' + product.productCode}} AS metadata
        ORDER BY purchaseScore DESC, searchScore DESC LIMIT 5

    """
    )

In [417]:
# Use the same tailored search recommendations as above but with a smaller limit
kg_recommendations_bot1 = Neo4jVector.from_existing_index(
    embedding=embedding_model,
    url=NEO4J_URI,
    username=NEO4J_USERNAME,
    password=NEO4J_PASSWORD,
    index_name='product-text-embeddings',
    retrieval_query="""
    WITH node as searchProduct, score as searchScore
    MATCH(searchProduct)<-[:VARIANT_OF]-(:Article)-[r:CUSTOMERS_ALSO_LIKE]->(:Article)-[:VARIANT_OF]-(product)
    WITH  product, searchScore, sum(r.score*searchScore) AS recommenderScore
    RETURN product.text + '\nurl: ' + 'https://representative-domain/product/' + product.productCode  AS text,
    recommenderScore AS score,
    {source: 'https://representative-domain/product/' + product.productCode} AS metadata
    ORDER BY score DESC LIMIT 5
    """
)

### Prompt Engineering
Now let's define our prompts. We will combine two together:
1. A system prompt which, in this case tells the LLM how to generated the message
2. Human prompt: In this case just wraps the search prompt entered by the customer

This will allow us to pass the customer search to the retrievers, but then also to the LLM for addition context when drafting the message.

In [418]:
general_system_template = '''
You are a personal assistant named Sally for a fashion, home, and beauty company called HRM.
write an email to {customerName}, one of your customers, to promote and summarize products relevant for them given the current season / time of year: {timeOfYear} .
Please only mention the Products listed below. Do not come up with or add any new products to the list.
Each product description comes with a "url" field. make sure to link to the url with descriptive name text for each product so the customer can easily find them.

---
# Relevant Products:
{searchProds}

# Customer May Also Be Interested In:
{recProds}
---
'''
general_user_template = "{searchPrompt}"
messages = [
    SystemMessagePromptTemplate.from_template(general_system_template),
    HumanMessagePromptTemplate.from_template(general_user_template),
]
prompt = ChatPromptTemplate.from_messages(messages)

### Create a Chain
Now let's put a chain together that will leverage the retrievers, prompts, and LLM model. This is where Langchain shines, putting RAG together in a simple way.

In addition to the personalized search and recommendations context, we will allow for som other parameters

1. `customerName`: Ordinarily this will be pulled from Neo4j, but it has been scrubbed from the data for obvious reasons so we will provide our own name here.
2. `timeOfYear`: The time of year as a date, season, month, etc. the LLM can tailor the language appropriately.

You can potentially add other creative parameters here to help the LLM write relevant messages.


In [419]:
# Helper function
def format_docs(docs):
    return "\n\n".join([d.page_content for d in docs])

def chain_gen(customer_id):
    return ({'searchProds': (lambda x:x['searchPrompt']) | kg_personalized_search_gen(customer_id).as_retriever(search_kwargs={"k": 100}) | format_docs,
              'recProds': (lambda x:x['searchPrompt']) | kg_recommendations_bot1.as_retriever(search_kwargs={"k": 5}) | format_docs,
              'customerName': lambda x:x['customerName'],
              'timeOfYear': lambda x:x['timeOfYear'],
              "searchPrompt":  lambda x:x['searchPrompt']}
             | prompt
             | llm
             | StrOutputParser())

### Examples Runs

In [420]:
chain = chain_gen(CUSTOMER_ID)

In [421]:
print(chain.invoke({'searchPrompt':search_prompt, 'customerName':'Alex Smith', 'timeOfYear':'Nov, 2023'}))

Dear Alex Smith,

I hope this email finds you well. As the weather gets cooler, it's the perfect time to update your wardrobe with cozy and stylish pieces. I wanted to share with you some of our latest products that I think you'll love, especially if you're a fan of oversized sweaters.

1. Queen Sweater: This lightweight sweatshirt fabric sweater features ribbing around the neckline, cuffs, and hem. It's perfect for layering or wearing on its own. You can find it [here](https://representative-domain/product/677930).

2. Jess oversize LS: Made from a soft jersey cotton blend, this oversized top is perfect for a relaxed and comfortable look. It has dropped shoulders and long sleeves, making it a versatile piece for any occasion. You can find it [here](https://representative-domain/product/516712).

3. Irma sweater: This printed sweatshirt fabric sweater features dropped shoulders, long sleeves, and ribbing around the neckline, cuffs, and hem. It adds a touch of style to your outfit while

In [422]:
print(chain.invoke({'searchPrompt':"western boots", 'customerName':'Alex Smith', 'timeOfYear':'Nov, 2023'}))

Dear Alex Smith,

I hope this email finds you well. As the weather gets colder and the holiday season approaches, I wanted to share with you some of our latest products that are perfect for this time of year.

Firstly, we have the "Harry hiking boot." These boots are made of sturdy cotton canvas with an ankle-height shaft, lacing at the front, and a loop at the back. They feature chunky, patterned soles and have a platform front of 4.5 cm and a 6 cm heel. You can find them [here](https://representative-domain/product/817484).

Another great option is the "Patsy Platform" boots. These platform boots are made of imitation leather and have a zip on one side, lacing at the front, and a loop at the back. They have decorative welt seams and chunky soles, with a platform front of 4 cm and a 5 cm heel. You can find them [here](https://representative-domain/product/752857).

If you're looking for a pair of jeans to complete your outfit, we have the "Bono NW slim denim." These ankle-length jeans

Feel free to experiment and try more!

### Demo App
Now lets use the above tools to create a demo app with Gradio.  We will need to make a couple more functions, but otherwise easy to fire up from a Notebook!

In [423]:
# Create a means to generate and cache chains...so we can quickly try different customer ids
personalized_search_chain_cache = dict()
def get_chain(customer_id):
    if customer_id in personalized_search_chain_cache:
        return personalized_search_chain_cache[customer_id]
    chain = chain_gen(customer_id)
    personalized_search_chain_cache[customer_id] = chain
    return chain

In [ ]:
import gradio as gr

def message_generator(*x):
    chain = get_chain(x[0])
    return chain.invoke({'searchPrompt':x[3], 'customerName':x[2], 'timeOfYear': x[1]})

customer_id = gr.Textbox(value=CUSTOMER_ID, label="Customer ID")
time_of_year = gr.Textbox(value="Nov, 2023", label="Time Of Year")
customer_name = gr.Textbox(value='Alex Smith', label="Customer Name")
search_prompt = gr.Textbox(value='Oversized Sweaters', label="Search Prompt(s)")
message_result = gr.Markdown( label="Message")

demo = gr.Interface(fn=message_generator, inputs=[customer_id, time_of_year, customer_name, search_prompt], outputs=message_result)
demo.launch(share=True, debug=True)

Running on local URL:  http://127.0.0.1:7860

Could not create share link. Missing file: /Users/zachblumenfeld/opt/anaconda3/envs/Downloads/lib/python3.10/site-packages/gradio/frpc_darwin_arm64_v0.2. 

Please check your internet connection. This can happen if your antivirus software blocks the download of this file. You can install manually by following these steps: 

1. Download this file: https://cdn-media.huggingface.co/frpc-gradio-0.2/frpc_darwin_arm64
2. Rename the downloaded file to: frpc_darwin_arm64_v0.2
3. Move the file to this location: /Users/zachblumenfeld/opt/anaconda3/envs/Downloads/lib/python3.10/site-packages/gradio


## Wrap Up